
### Purpose
To find all significantl pCRE (putative cis-regulatory elements) present upstream 1000bp of dehydration differentially regulated genes. Scripts are adapted from https://github.com/ShiuLab/MotifDiscovery/blob/master/RandomForest_v2.0.py
### Input
- Positive gene list
- Negative gene list

### Output
- A dataframe (.csv) with all pCREs (present: 1; absent: 0)
- A txt file with all significant pCRES with p-value or adjust.p-value 

### Steps

- A set of all possible 6-mer oligomers was evaluated for their enrichment among genes in each wound response cluster compared with nonresponsive genes. Only the 5-mers with significant enrichment (p-value < 0.01) were retained for the next step. 
- The sequence of each significantly enriched 6-mer from step 1 was extended with 1 nucleotide in either direction, the resulting extended k-mer was examined for enrichment, and the significantly enriched ones (p-value < 0.01) were retained. Iteratively extend one bp until no more enriched kmers. 

*Noted that if two k-mers were both significantly enriched and one k-mer sequence exactly matched the other one, only the one with lower adjusted P value was retained. 

*Adapted from https://doi.org/10.1105/tpc.18.00194

*If use adjust.p-value, uncomment calculate_p_adjust(pvalues) in find_enrich()

### Difference from kmersFinding5
- Extended kmer is retained only when the p-value is smaller than its parent kmer



In [1]:
from Bio import SeqIO
from Bio.Seq import Seq
from scipy.stats import fisher_exact
from itertools import combinations_with_replacement
import itertools
import numpy as np
import pandas as pd
import re
import copy

In [3]:
########################################## Generate a fasta file ##############################################################
def fastaGenerator(geneList, fileName):
    ## extract 1000pb promoter from TAIR10_upstream_1000 
    seq_records = []
    for seq_record in SeqIO.parse("TAIR10_upstream_1000_20101104", "fasta"):
        if seq_record.id in geneList:
            seq_records.append(seq_record)
            
#     # when sample same number of genes
#     while len(seq_records) < len(geneList) and 'positive' not in fileName:
#         extra = np.random.choice(allNegativeGeneList,len(geneList)-len(seq_records)).tolist()
#         for seq_record in SeqIO.parse("TAIR10_upstream_1000_20101104", "fasta"):
#             if seq_record.id in extra and seq_record.id not in geneList:
#                 seq_records.append(seq_record)
    SeqIO.write(seq_records, fileName, 'fasta')
    
########################################## Find all present kmers ############################################################
# adapted from https://github.com/ShiuLab/MotifDiscovery/blob/master/RandomForest_v2.0.py
def find_kmers(afastafile, km):
    
    print('Looking for kmers!!!')
    df = pd.DataFrame(columns=km,dtype=int)
    for seq_record in SeqIO.parse(afastafile, 'fasta'):
        seq = str(seq_record.seq)
        genes_array = []       
        # iterate each CRE
        '''
        ### consider the number of CRE
        for ki in km:
            kmer = Seq(ki)
            if str(kmer) in seq or str(kmer.reverse_complement()) in seq: # find all occurence of kmer in the promoter including reverse complement
                occurence = [m for m in re.finditer(str(kmer), seq)] # [m for m.start() in re.finditer(str(kmer), seq)] also ok
                occurence_rev = [m for m in re.finditer(str(kmer.reverse_complement()), seq)]
                genes_array.append(len(occurence+occurence_rev))
            else:
                genes_array.append(0)
        '''      
        ### Not consider occurence number
        for ki in km:
            kmer = Seq(ki)
            if str(kmer) in seq or str(kmer.reverse_complement()) in seq: # find all occurence of kmer in the promoter including reverse complement
                genes_array.append(1)
            else:
                genes_array.append(0)
        # add counting to the dataframe 
        df.loc[seq_record.id] = genes_array
            
    return df
    
########################################## Calculate p-value or adjust.p-value ################################################
def calculate_pvalue(df_pos,df_neg):
    # try except ValueError
    fet_pvalue = {}
    for col in df_pos.columns:
        try:
            TP = df_pos[col].sum()                   #Positive Examples with kmer present
            FP = df_neg[col].sum()                   #Negative Examples with kmer present
            TN = df_neg[df_neg[col]==0].shape[0]     #Negative Examples without kmer
            FN = df_pos[df_pos[col]==0].shape[0]     #Positive Examples without kmer
            print([[TP,FN],[FP,TN]])
            oddsratio,pvalue = fisher_exact([[TP,FN],[FP,TN]],alternative='greater') # one tail Fisher exact test
            fet_pvalue[col] = pvalue
        except ValueError:
            fet_pvalue[col] = 1.0
            
    # return a dictionary   
    return fet_pvalue

def calculate_p_adjust(pvalue_dict):
    # input a dictionary
    from rpy2.robjects.packages import importr
    from rpy2.robjects.vectors import FloatVector

    stats = importr('stats')
    p_adjust = stats.p_adjust(FloatVector(list(pvalue_dict.values())), method = 'BH')
    # return a dictionary
    return dict(zip(list(pvalue_dict.keys()),list(p_adjust)))

########################################## Find significant kmers with FISHER-exact-test #####################################
def find_enrich(km):
    # file needs to be opened every time
    print('Find enriched kmers!!!')
    P = open('positiveFasta','r')
    N = open('negativeFasta','r')
   
    df_pos = find_kmers(P, km)
    df_neg = find_kmers(N, km)
    
    pvalues = calculate_pvalue(df_pos,df_neg) 
    ## calculate adjust.p-value
#     pvalues = calculate_p_adjust(pvalues)

    # drop the CRE is the pvalue is larger than the threshold
    drop_col = [col for col in pvalues if pvalues[col] >= 0.01]
    list(map(pvalues.pop, drop_col)) # remove elements with keys in drop_col
    if len(pvalues)>0:
        df_pos = df_pos.drop(columns = drop_col)
    return df_pos, pvalues

def find_enrich2(df_pos, df_neg):

    pvalues = calculate_pvalue(df_pos,df_neg) 
    # drop the CRE is the pvalue is larger than the threshold
    drop_col = [col for col in pvalues if pvalues[col] >= 0.01]
    df_pos = df_pos.drop(columns = drop_col)
    list(map(pvalues.pop, drop_col)) # remove elements with keys in drop_col
    
    return df_pos, pvalues
################################# Extend kmers by one bp until no more kmers significantly present #############################
def kmers_extension(posGeneList,enriched):
    ''' 1, extend one bp to kmers from last step
        2, calculate pvalue
        3, accept extended kmer if pvalue is smaller than its parent kmer
    ''' 
    kmers = {}
    df = pd.DataFrame(index=posGeneList)
    
    for key in enriched:
        temp_km = [key+"A", key+"T", key+"G", key+"C", "A"+key, "T"+key, "G"+key, "C"+key]
        df_tmp, new_enriched = find_enrich(temp_km)
        print('Before comparing:\n')
        print(new_enriched)
        if len(new_enriched) > 0:               
            for k in new_enriched:
                if new_enriched[k] < enriched[key]:
                    df[k] = df_tmp[k].values
                    kmers[k] = new_enriched[k]
        print('After comparing:\n')
        print(kmers)
                
    return df, kmers
    
################################### Main function to find enriched kmers for each cluster ################################################
def main(geneCluster):
    
    # read and create a positive gene fasta file
    with open('geneClusters/'+geneCluster,'r') as aFile:
        posGeneList = aFile.read().splitlines()
    fastaGenerator(posGeneList, 'positiveFasta')
    # file needs to be opened every time
    with open('positiveFasta','r') as Pos:
        df_positive = find_kmers(Pos, all6mers)
        
    # empty dataframe to hold results    
    dfAllKmers = pd.DataFrame(index=posGeneList)
    dfPvalue = pd.DataFrame(columns=['features','p-value'])
    
    # find significantly enriched 6-mers
    df_kmer, kmer_pvalue = find_enrich2(df_positive,df_allNegative)
    dfAllKmers = pd.concat([dfAllKmers,df_kmer],axis=1)
    #convert the dictionary to a dataframe
    adf = pd.DataFrame({'features':list(kmer_pvalue.keys()),'p-value':list(kmer_pvalue.values())})
    dfPvalue = pd.concat([dfPvalue,adf],axis=0)
    
    ## get all kmers until no kmers can be extended
    kmer_dict = copy.copy(kmer_pvalue)
    while len(kmer_dict) > 0:
        df_kmer, kmer_dict = kmers_extension(posGeneList,kmer_dict)
        if len(kmer_dict)>0:
            dfAllKmers = pd.concat([dfAllKmers,df_kmer],axis=1)
            bdf = pd.DataFrame({'features':list(kmer_dict.keys()),'p-value':list(kmer_dict.values())})
            dfPvalue = pd.concat([dfPvalue,bdf],axis=0)
    print('*'*100)
    print()
    print('*'*100)
                          
    dfAllKmers.to_csv('originalResults/noRepeat_with_allNegative/df_'+geneCluster.split('.txt')[0]+'.csv')
    dfPvalue.to_csv('originalResults/noRepeat_with_allNegative/pValue_'+geneCluster.split('.txt')[0]+'.csv')

In [4]:
# generate genelist by cluster
data = pd.read_csv('dehydration_fc2_scaled_clustered.csv') # use data with |log(FC)|>=2

for i in range(1,len(data.clust.unique())+1):
    genelist = data[data.clust=='Cluster '+str(i)].GeneID.tolist()
    with open('geneClusters/cluster_'+ str(i)+'.txt', "w") as file:
        for mer in genelist:
            file.write(mer + '\n')

with open('all6mers.txt','r') as aFile:
    all6mers = aFile.read().splitlines()

with open('negativeGeneList_rmStressDEG.txt','r') as aFile:
    allNegativeGeneList = aFile.read().splitlines() 
fastaGenerator(allNegativeGeneList, 'negativeFasta')

with open('negativeFasta','r') as negativeFasta:
    df_allNegative = find_kmers(negativeFasta, all6mers)

if __name__ == "__main__":
    from os import listdir
    for file in listdir('geneClusters/'): # in case clusters changed
        main(file)

Looking for kmers!!!
Looking for kmers!!!
[[92, 2], [2963, 190]]
[[92, 2], [2937, 216]]
[[80, 14], [2848, 305]]
[[93, 1], [2833, 320]]
[[90, 4], [2836, 317]]
[[89, 5], [2814, 339]]
[[79, 15], [2629, 524]]
[[83, 11], [2588, 565]]
[[88, 6], [2923, 230]]
[[79, 15], [2638, 515]]
[[69, 25], [2262, 891]]
[[56, 38], [1721, 1432]]
[[86, 8], [2840, 313]]
[[78, 16], [2492, 661]]
[[59, 35], [1880, 1273]]
[[65, 29], [1997, 1156]]
[[89, 5], [2830, 323]]
[[87, 7], [2677, 476]]
[[66, 28], [1978, 1175]]
[[68, 26], [2076, 1077]]
[[86, 8], [2694, 459]]
[[72, 22], [2313, 840]]
[[68, 26], [2303, 850]]
[[79, 15], [2411, 742]]
[[82, 12], [2597, 556]]
[[72, 22], [2459, 694]]
[[45, 49], [1779, 1374]]
[[33, 61], [1344, 1809]]
[[81, 13], [2453, 700]]
[[80, 14], [2393, 760]]
[[44, 50], [1414, 1739]]
[[56, 38], [1905, 1248]]
[[85, 9], [2917, 236]]
[[77, 17], [2515, 638]]
[[67, 27], [1991, 1162]]
[[54, 40], [1852, 1301]]
[[73, 21], [2374, 779]]
[[73, 21], [2535, 618]]
[[51, 43], [1972, 1181]]
[[42, 52], [1669, 148

[[82, 12], [2456, 697]]
[[84, 10], [2637, 516]]
[[62, 32], [1906, 1247]]
[[58, 36], [1926, 1227]]
[[84, 10], [2687, 466]]
[[92, 2], [2937, 216]]
[[79, 15], [2606, 547]]
[[86, 8], [2695, 458]]
[[71, 23], [2407, 746]]
[[76, 18], [2488, 665]]
[[47, 47], [1596, 1557]]
[[31, 63], [1239, 1914]]
[[76, 18], [2506, 647]]
[[80, 14], [2552, 601]]
[[46, 48], [1564, 1589]]
[[68, 26], [2043, 1110]]
[[68, 26], [2347, 806]]
[[62, 32], [2199, 954]]
[[47, 47], [1499, 1654]]
[[38, 56], [1216, 1937]]
[[51, 43], [1704, 1449]]
[[69, 25], [2305, 848]]
[[51, 43], [1803, 1350]]
[[32, 62], [1234, 1919]]
[[42, 52], [1548, 1605]]
[[41, 53], [1295, 1858]]
[[16, 78], [795, 2358]]
[[21, 73], [633, 2520]]
[[37, 57], [1166, 1987]]
[[34, 60], [1164, 1989]]
[[13, 81], [513, 2640]]
[[15, 79], [648, 2505]]
[[75, 19], [2318, 835]]
[[59, 35], [2244, 909]]
[[37, 57], [1303, 1850]]
[[46, 48], [1499, 1654]]
[[57, 37], [1871, 1282]]
[[74, 20], [2440, 713]]
[[45, 49], [1303, 1850]]
[[59, 35], [1524, 1629]]
[[47, 47], [1346, 1807

[[21, 73], [613, 2540]]
[[8, 86], [334, 2819]]
[[29, 65], [925, 2228]]
[[23, 71], [837, 2316]]
[[17, 77], [509, 2644]]
[[5, 89], [303, 2850]]
[[28, 66], [546, 2607]]
[[11, 83], [387, 2766]]
[[4, 90], [190, 2963]]
[[6, 88], [139, 3014]]
[[8, 86], [432, 2721]]
[[6, 88], [311, 2842]]
[[9, 85], [239, 2914]]
[[7, 87], [236, 2917]]
[[22, 72], [872, 2281]]
[[16, 78], [709, 2444]]
[[21, 73], [470, 2683]]
[[7, 87], [499, 2654]]
[[11, 83], [522, 2631]]
[[24, 70], [797, 2356]]
[[13, 81], [461, 2692]]
[[7, 87], [382, 2771]]
[[8, 86], [369, 2784]]
[[5, 89], [314, 2839]]
[[8, 86], [288, 2865]]
[[4, 90], [181, 2972]]
[[14, 80], [681, 2472]]
[[10, 84], [335, 2818]]
[[8, 86], [302, 2851]]
[[6, 88], [275, 2878]]
[[57, 37], [1527, 1626]]
[[34, 60], [1164, 1989]]
[[18, 76], [756, 2397]]
[[27, 67], [971, 2182]]
[[31, 63], [830, 2323]]
[[24, 70], [1072, 2081]]
[[15, 79], [664, 2489]]
[[20, 74], [774, 2379]]
[[23, 71], [804, 2349]]
[[25, 69], [598, 2555]]
[[19, 75], [442, 2711]]
[[18, 76], [614, 2539]]
[[24,

[[14, 80], [397, 2756]]
[[9, 85], [345, 2808]]
[[9, 85], [374, 2779]]
[[4, 90], [388, 2765]]
[[6, 88], [205, 2948]]
[[3, 91], [122, 3031]]
[[13, 81], [525, 2628]]
[[11, 83], [387, 2766]]
[[3, 91], [169, 2984]]
[[4, 90], [168, 2985]]
[[89, 5], [2887, 266]]
[[84, 10], [2687, 466]]
[[79, 15], [2422, 731]]
[[70, 24], [2283, 870]]
[[82, 12], [2551, 602]]
[[79, 15], [2510, 643]]
[[61, 33], [1952, 1201]]
[[65, 29], [1922, 1231]]
[[70, 24], [2298, 855]]
[[60, 34], [2032, 1121]]
[[49, 45], [1771, 1382]]
[[39, 55], [1036, 2117]]
[[69, 25], [2310, 843]]
[[63, 31], [1869, 1284]]
[[37, 57], [1342, 1811]]
[[38, 56], [1254, 1899]]
[[81, 13], [2482, 671]]
[[74, 20], [2349, 804]]
[[51, 43], [1499, 1654]]
[[35, 59], [1434, 1719]]
[[65, 29], [1867, 1286]]
[[86, 8], [2694, 459]]
[[54, 40], [1804, 1349]]
[[57, 37], [1945, 1208]]
[[68, 26], [2046, 1107]]
[[59, 35], [1957, 1196]]
[[29, 65], [1134, 2019]]
[[27, 67], [879, 2274]]
[[55, 39], [1898, 1255]]
[[68, 26], [1919, 1234]]
[[30, 64], [955, 2198]]
[[45, 4

[[45, 49], [1421, 1732]]
[[32, 62], [1040, 2113]]
[[61, 33], [2120, 1033]]
[[72, 22], [2233, 920]]
[[33, 61], [1361, 1792]]
[[48, 46], [1496, 1657]]
[[87, 7], [2743, 410]]
[[90, 4], [2865, 288]]
[[68, 26], [2249, 904]]
[[76, 18], [2301, 852]]
[[89, 5], [2887, 266]]
[[92, 2], [2963, 190]]
[[92, 2], [2852, 301]]
[[88, 6], [2919, 234]]
[[80, 14], [2670, 483]]
[[88, 6], [2953, 200]]
[[67, 27], [2158, 995]]
[[55, 39], [1529, 1624]]
[[87, 7], [2714, 439]]
[[92, 2], [2933, 220]]
[[60, 34], [2006, 1147]]
[[78, 16], [2526, 627]]
[[84, 10], [2604, 549]]
[[70, 24], [2563, 590]]
[[64, 30], [1828, 1325]]
[[50, 44], [1719, 1434]]
[[70, 24], [2305, 848]]
[[91, 3], [2988, 165]]
[[74, 20], [2441, 712]]
[[57, 37], [1892, 1261]]
[[61, 33], [1959, 1194]]
[[51, 43], [1971, 1182]]
[[40, 54], [1316, 1837]]
[[30, 64], [937, 2216]]
[[43, 51], [1405, 1748]]
[[57, 37], [1527, 1626]]
[[19, 75], [662, 2491]]
[[22, 72], [890, 2263]]
[[81, 13], [2662, 491]]
[[83, 11], [2712, 441]]
[[56, 38], [1864, 1289]]
[[58, 36],

...

[[38, 35], [1108, 2045]]
[[22, 51], [813, 2340]]
[[17, 56], [342, 2811]]
[[13, 60], [465, 2688]]
[[32, 41], [1024, 2129]]
[[25, 48], [745, 2408]]
[[11, 62], [409, 2744]]
[[19, 54], [589, 2564]]
{'AAATACA': 0.0025143467333737174, 'AAATACG': 0.0020827926716954132}
Find enriched kmers!!!
Looking for kmers!!!
Looking for kmers!!!
[[13, 60], [375, 2778]]
[[18, 55], [276, 2877]]
[[4, 69], [137, 3016]]
[[1, 72], [116, 3037]]
[[17, 56], [342, 2811]]
[[12, 61], [232, 2921]]
[[3, 70], [170, 2983]]
[[4, 69], [174, 2979]]
{'AATACGT': 5.938570831150573e-05, 'AAATACG': 0.0020827926716954132, 'TAATACG': 0.007681808831001164}
Find enriched kmers!!!
Looking for kmers!!!
Looking for kmers!!!
[[15, 58], [291, 2862]]
[[8, 65], [229, 2924]]
[[2, 71], [95, 3058]]
[[3, 70], [115, 3038]]
[[8, 65], [256, 2897]]
[[6, 67], [173, 2980]]
[[7, 66], [106, 3047]]
[[6, 67], [211, 2942]]
{'AATGCCA': 0.002854892022647385}
Find enriched kmers!!!
Looking for kmers!!!
Looking for kmers!!!
[[4, 69], [197, 2956]]
[[10, 63], 

[[20, 53], [719, 2434]]
[[32, 41], [1008, 2145]]
[[15, 58], [521, 2632]]
[[4, 69], [406, 2747]]
[[21, 52], [903, 2250]]
[[26, 47], [854, 2299]]
[[12, 61], [465, 2688]]
[[14, 59], [439, 2714]]
{}
Find enriched kmers!!!
Looking for kmers!!!
Looking for kmers!!!
[[12, 61], [415, 2738]]
[[11, 62], [382, 2771]]
[[7, 66], [120, 3033]]
[[6, 67], [173, 2980]]
[[10, 63], [326, 2827]]
[[14, 59], [358, 2795]]
[[4, 69], [195, 2958]]
[[7, 66], [214, 2939]]
{}
Find enriched kmers!!!
Looking for kmers!!!
Looking for kmers!!!
[[16, 57], [514, 2639]]
[[16, 57], [453, 2700]]
[[6, 67], [164, 2989]]
[[6, 67], [264, 2889]]
[[11, 62], [486, 2667]]
[[13, 60], [454, 2699]]
[[9, 64], [218, 2935]]
[[10, 63], [234, 2919]]
{}
Find enriched kmers!!!
Looking for kmers!!!
Looking for kmers!!!
[[22, 51], [746, 2407]]
[[27, 46], [909, 2244]]
[[20, 53], [488, 2665]]
[[14, 59], [424, 2729]]
[[25, 48], [846, 2307]]
[[29, 44], [915, 2238]]
[[10, 63], [342, 2811]]
[[18, 55], [462, 2691]]
{'TACAATG': 0.00717865815986307}
Fi

[[8, 65], [176, 2977]]
[[15, 58], [182, 2971]]
[[5, 68], [94, 3059]]
[[4, 69], [103, 3050]]
[[21, 52], [229, 2924]]
[[4, 69], [165, 2988]]
[[1, 72], [79, 3074]]
[[3, 70], [69, 3084]]
{'CGTGTCT': 2.2360069567726728e-05, 'ACGTGTC': 5.788574120532308e-08}
Find enriched kmers!!!
Looking for kmers!!!
Looking for kmers!!!
[[4, 69], [90, 3063]]
[[11, 62], [159, 2994]]
[[5, 68], [132, 3021]]
[[1, 72], [97, 3056]]
[[11, 62], [163, 2990]]
[[4, 69], [170, 2983]]
[[4, 69], [72, 3081]]
[[0, 73], [67, 3086]]
{'CGTGGTT': 0.0012869672295009813, 'ACGTGGT': 0.0015575052779951632}
Find enriched kmers!!!
Looking for kmers!!!
Looking for kmers!!!
[[10, 63], [163, 2990]]
[[5, 68], [123, 3030]]
[[7, 66], [61, 3092]]
[[2, 71], [63, 3090]]
[[16, 57], [203, 2950]]
[[5, 68], [101, 3052]]
[[2, 71], [38, 3115]]
[[0, 73], [54, 3099]]
{'CGTGGCA': 0.004958911660472485, 'CGTGGCG': 0.0007313593594573856, 'ACGTGGC': 1.9142344911078794e-05}
Find enriched kmers!!!
Looking for kmers!!!
Looking for kmers!!!
[[7, 66], [120, 

[[9, 64], [265, 2888]]
[[13, 60], [230, 2923]]
[[5, 68], [126, 3027]]
[[6, 67], [115, 3038]]
[[12, 61], [300, 2853]]
[[7, 66], [179, 2974]]
[[5, 68], [127, 3026]]
[[7, 66], [136, 3017]]
{'AACATTGT': 0.002636057268978953}
Find enriched kmers!!!
Looking for kmers!!!
Looking for kmers!!!
[[1, 72], [42, 3111]]
[[3, 70], [51, 3102]]
[[5, 68], [37, 3116]]
[[3, 70], [40, 3113]]
[[8, 65], [65, 3088]]
[[2, 71], [24, 3129]]
[[0, 73], [36, 3117]]
[[2, 71], [47, 3106]]
{'ACCACGTG': 0.002290121639549703, 'AACCACGT': 0.0001927321010859709}
Find enriched kmers!!!
Looking for kmers!!!
Looking for kmers!!!
[[2, 71], [59, 3094]]
[[8, 65], [65, 3088]]
[[0, 73], [17, 3136]]
[[1, 72], [20, 3133]]
[[4, 69], [60, 3093]]
[[4, 69], [42, 3111]]
[[1, 72], [29, 3124]]
[[2, 71], [28, 3125]]
{'AACCACGT': 0.0001927321010859709}
Find enriched kmers!!!
Looking for kmers!!!
Looking for kmers!!!
[[2, 71], [85, 3068]]
[[6, 67], [120, 3033]]
[[4, 69], [50, 3103]]
[[5, 68], [65, 3088]]
[[5, 68], [108, 3045]]
[[2, 71], [109

[[6, 67], [101, 3052]]
[[8, 65], [153, 3000]]
[[3, 70], [64, 3089]]
[[2, 71], [57, 3096]]
[[4, 69], [118, 3035]]
[[5, 68], [142, 3011]]
[[8, 65], [66, 3087]]
[[2, 71], [40, 3113]]
{'GGTACATT': 0.00021220867258908704}
Find enriched kmers!!!
Looking for kmers!!!
Looking for kmers!!!
[[3, 70], [21, 3132]]
[[1, 72], [27, 3126]]
[[1, 72], [16, 3137]]
[[2, 71], [19, 3134]]
[[0, 73], [17, 3136]]
[[0, 73], [31, 3122]]
[[4, 69], [19, 3134]]
[[3, 70], [16, 3137]]
{'GGTACGTC': 0.00154308833211068, 'CGTACGTC': 0.008304022058950738}
Find enriched kmers!!!
Looking for kmers!!!
Looking for kmers!!!
[[3, 70], [55, 3098]]
[[0, 73], [42, 3111]]
[[0, 73], [9, 3144]]
[[5, 68], [16, 3137]]
[[3, 70], [31, 3122]]
[[0, 73], [49, 3104]]
[[3, 70], [28, 3125]]
[[2, 71], [15, 3138]]
{'GGTCCCAC': 7.93110238490103e-05}
Find enriched kmers!!!
Looking for kmers!!!
Looking for kmers!!!
[[2, 71], [47, 3106]]
[[5, 68], [56, 3097]]
[[3, 70], [38, 3115]]
[[0, 73], [28, 3125]]
[[7, 66], [106, 3047]]
[[2, 71], [35, 3118]]
[